In [1]:
import sys
import SimpleITK as sitk
import matplotlib.pyplot as plt
from matplotlib.gridspec import GridSpec
%matplotlib inline 

import numpy as np
from numpy import array, zeros_like
from scipy.ndimage import zoom

import os
import fnmatch
import shutil
from ipywidgets import interact, fixed
import pandas as pd
from pathlib import Path

from skimage import data
from skimage import color
from skimage import img_as_float
from skimage import exposure
from skimage import data, color
from skimage.transform import rescale, resize, downscale_local_mean, pyramid_expand
from skimage.transform import rotate
from skimage import io
from scipy.ndimage import rotate as rotate_nd
from skimage import img_as_ubyte
from PIL import Image

#parallel computing packages
from numba import jit
import psutil
from multiprocess import Pool

#function for showing volume images
def myshow(image_arr,slice_n):
    plt.imshow(image_arr[slice_n,:,:],cmap='gray')
    plt.show()

In [2]:
df=pd.read_pickle('/mnt/e/Image Processing/Brats Project/final_pickle.pkl')

In [3]:
from sklearn.model_selection import train_test_split

train, test = train_test_split(df, test_size=0.25)

## Rescaling to [ 0,1 ]

In [ ]:
def rescale_to(data,col, newmin_value=0, newmax_value=1):
    
    def to_norm(array, newmin = newmin_value, newmax=newmax_value): 
        norm_arr=(array - array.min()) * ((newmax - newmin) / (array.max() - array.min())) + newmin
        return norm_arr
    
    def go_and_norm():
        for i,y in enumerate(data.loc[:, col]):
            data.at[i, col] = to_norm(y)
            print('making {} for you ...'.format(i))
    
    go_and_norm()
    print('All done.')






In [ ]:
rescale_to(df, 'X')

## Data Augmentation 

In [ ]:
#check for only tumor indexes, to augment only images with tumors
def check_tumor(data, col): 
    indexes = []
    counter=0
    for i,y in enumerate(data.loc[:, col]): 
        if len(np.unique(y)) == 4:
            print(i)
            indexes.append(i)
            counter += 1
    print('All done!The number of images with tumors is {} and number of images without tumor is {}'.format(counter, len(data.index)-counter))
    return indexes




def go_and_augment(data,indexes, col=['X', 'Y'], augmentation = ['hor_flip','vert_flip', 'rotate_10_m10']):
    counter = len(data.index)
    
    for index, image in enumerate(data.loc[:, col[0]]):
        
        if index in indexes:
            
            #augmented_image = np.zeros((240,240,3), dtype='uint8') #empty arrays for augmented image
            #augmented_label = np.zeros((240,240), dtype='uint8') #for labels
            
            if augmentation[0]=='hor_flip':
                augmented_image = image[:, ::-1]
                augmented_label = data.loc[index, col[1]][:, ::-1]
                
                data.at[counter, col[0]] = augmented_image
                data.at[counter, col[1]] = augmented_label
            
                print('{} {} DONE!...images added to {}'.format(index, augmentation[0], counter))
                counter += 1
                
            if augmentation[1]=='vert_flip':
                augmented_image=image[::-1, :]
                augmented_label = data.loc[index, col[1]][::-1, :]
                
                data.at[counter, col[0]] = augmented_image
                data.at[counter, col[1]] = augmented_label
                
                
                print('{} {} DONE!...'.format(index, augmentation[1], counter))
                counter += 1
            
            if augmentation[2]=='rotate_10_m10':
                
                augmented_image=rotate(image, -10)
                augmented_label=rotate(data.loc[index, col[1]], -10)
                
                data.at[counter, col[0]] = augmented_image
                data.at[counter, col[1]] = augmented_label
                counter += 1
                print('{} {} DONE!...'.format(index, augmentation[2], counter))
                
                augmented_image=rotate(image, 10)
                augmented_label=rotate(data.loc[index, col[1]], 10)
                
                data.at[counter, col[0]] = augmented_image
                data.at[counter, col[1]] = augmented_label
                counter += 1
                print('{} {} DONE!...'.format(index, augmentation[2], counter))
            
            
df = df.append(df.iloc[0], ignore_index=True)            
            
            
            
            

In [ ]:
ind = check_tumor(df, 'Y') #creating list of indexes to augment

go_and_augment(df, ind) #go and augment, rotations 10 -10, vertical and horizontal flips! images and labels

In [ ]:
image=df.X[56896]
label=df.Y[56896]

In [ ]:
plt.imshow(image)

In [ ]:
plt.imshow(label)

## Augmenting dataset with 'edema' images 

In [17]:
#images
@jit
def get_edema_images(data, col='X'):



    for i in range(len(edema_index)):
        
        b = data.loc[edema_index[i], col]
        lx, ly, lz = b.shape
        roi=b[lx // 4: - lx // 4, ly // 4: - ly // 4] #sacling brain to receive bigger picture 
    
        im = pyramid_expand(roi, upscale=2, sigma=0, order=0, mode='constant', cval=0, multichannel=True)
    
        img = img_as_ubyte(im)
        print('{} DONE!'.format(edema_index[i]))
    
    
    
    
        name=str(edema_index[i])+'.png'
        io.imsave('/mnt/e/Image Processing/Brats Project/data/images_train/'+name, img)     
        print('{} image saved to corresponding directory!'.format(edema_index[i]))

In [18]:
#labels
@jit
def get_edema_labels(data, col='Y'):
    
    
    
    for i in range(len(edema_index)):
        b = data.loc[edema_index[i], col]
        lx, ly = b.shape
        roi=b[lx // 4: - lx // 4, ly // 4: - ly // 4] #sacling brain to receive bigger picture 
        im = pyramid_expand(roi, upscale=2, sigma=0, order=0, mode='constant', cval=0, multichannel=False)
        lab=img_as_ubyte(im)
        print('{} DONE!'.format(edema_index[i]))
        
        
        name=str(edema_index[i])+'.png'
        io.imsave('/mnt/e/Image Processing/Brats Project/data/masks_train/'+name, lab)     
        print('{} image saved to corresponding directory!'.format(edema_index[i]))
        
    
    

In [6]:
#adding to our training dataset edema images only to improve edema segmentation 

edema_index = []
values = [0,2]
for i,y in enumerate(train.loc[:, 'Y']):
    l=np.isin(values, y)
    if l.all()==True and len(np.unique(y)) == 2:
        edema_index.append(train.index[i])

In [19]:
get_edema_images(train)
get_edema_labels(train)

/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/util/dtype.py:130: UserWarning: Possible precision loss when converting from float64 to uint8
  .format(dtypeobj_in, dtypeobj_out))


29745 DONE!
29745 image saved to corresponding directory!
20582 DONE!
20582 image saved to corresponding directory!
9298 DONE!
9298 image saved to corresponding directory!
3447 DONE!
3447 image saved to corresponding directory!
28573 DONE!
28573 image saved to corresponding directory!
22067 DONE!
22067 image saved to corresponding directory!
10891 DONE!
10891 image saved to corresponding directory!
10966 DONE!
10966 image saved to corresponding directory!
5377 DONE!
5377 image saved to corresponding directory!
19709 DONE!
19709 image saved to corresponding directory!
35774 DONE!
35774 image saved to corresponding directory!
16234 DONE!
16234 image saved to corresponding directory!
29182 DONE!
29182 image saved to corresponding directory!
18967 DONE!
18967 image saved to corresponding directory!
4896 DONE!
4896 image saved to corresponding directory!
11240 DONE!
11240 image saved to corresponding directory!
29998 DONE!
29998 image saved to corresponding directory!
18553 DONE!
18553 imag

3573 image saved to corresponding directory!
22582 DONE!
22582 image saved to corresponding directory!
24274 DONE!
24274 image saved to corresponding directory!
22938 DONE!
22938 image saved to corresponding directory!
4056 DONE!
4056 image saved to corresponding directory!
13692 DONE!
13692 image saved to corresponding directory!
25725 DONE!
25725 image saved to corresponding directory!
8264 DONE!
8264 image saved to corresponding directory!
12049 DONE!
12049 image saved to corresponding directory!
36179 DONE!
36179 image saved to corresponding directory!
19198 DONE!
19198 image saved to corresponding directory!
12241 DONE!
12241 image saved to corresponding directory!
20484 DONE!
20484 image saved to corresponding directory!
6170 DONE!
6170 image saved to corresponding directory!
10216 DONE!
10216 image saved to corresponding directory!
5523 DONE!
5523 image saved to corresponding directory!
24022 DONE!
24022 image saved to corresponding directory!
34565 DONE!
34565 image saved to co

33855 image saved to corresponding directory!
15853 DONE!
15853 image saved to corresponding directory!
832 DONE!
832 image saved to corresponding directory!
24530 DONE!
24530 image saved to corresponding directory!
24660 DONE!
24660 image saved to corresponding directory!
10881 DONE!
10881 image saved to corresponding directory!
25146 DONE!
25146 image saved to corresponding directory!
908 DONE!
908 image saved to corresponding directory!
23357 DONE!
23357 image saved to corresponding directory!
34098 DONE!
34098 image saved to corresponding directory!
30137 DONE!
30137 image saved to corresponding directory!
30080 DONE!
30080 image saved to corresponding directory!
35771 DONE!
35771 image saved to corresponding directory!
3368 DONE!
3368 image saved to corresponding directory!
18954 DONE!
18954 image saved to corresponding directory!
23639 DONE!
23639 image saved to corresponding directory!
21822 DONE!
21822 image saved to corresponding directory!
10870 DONE!
10870 image saved to cor

2152 image saved to corresponding directory!
9473 DONE!
9473 image saved to corresponding directory!
6331 DONE!
6331 image saved to corresponding directory!
31246 DONE!
31246 image saved to corresponding directory!
29228 DONE!
29228 image saved to corresponding directory!
15954 DONE!
15954 image saved to corresponding directory!
34725 DONE!
34725 image saved to corresponding directory!
10436 DONE!
10436 image saved to corresponding directory!
9295 DONE!
9295 image saved to corresponding directory!
14475 DONE!
14475 image saved to corresponding directory!
18446 DONE!
18446 image saved to corresponding directory!
19541 DONE!
19541 image saved to corresponding directory!
1090 DONE!
1090 image saved to corresponding directory!
26963 DONE!
26963 image saved to corresponding directory!
5442 DONE!
5442 image saved to corresponding directory!
1681 DONE!
1681 image saved to corresponding directory!
5938 DONE!
5938 image saved to corresponding directory!
30197 DONE!
30197 image saved to correspo

...

/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/5312.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/15143.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/36699.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/6326.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats P

17218 DONE!
17218 image saved to corresponding directory!
14192 DONE!
14192 image saved to corresponding directory!
25957 DONE!
25957 image saved to corresponding directory!
10646 DONE!
10646 image saved to corresponding directory!
24202 DONE!
24202 image saved to corresponding directory!
19200 DONE!
19200 image saved to corresponding directory!
25440 DONE!
25440 image saved to corresponding directory!
18568 DONE!
18568 image saved to corresponding directory!
20749 DONE!
20749 image saved to corresponding directory!
10994 DONE!
10994 image saved to corresponding directory!
4520 DONE!
4520 image saved to corresponding directory!
4857 DONE!
4857 image saved to corresponding directory!
611 DONE!
611 image saved to corresponding directory!
87 DONE!
87 image saved to corresponding directory!
8740 DONE!
8740 image saved to corresponding directory!
10987 DONE!
10987 image saved to corresponding directory!
7633 DONE!
7633 image saved to corresponding directory!
18002 DONE!
18002 image saved to

/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/4520.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/4857.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/611.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/87.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Projec

17541 DONE!
17541 image saved to corresponding directory!
17536 DONE!
17536 image saved to corresponding directory!
15882 DONE!
15882 image saved to corresponding directory!
4501 DONE!
4501 image saved to corresponding directory!
14006 DONE!
14006 image saved to corresponding directory!
30492 DONE!
30492 image saved to corresponding directory!
11101 DONE!
11101 image saved to corresponding directory!
3406 DONE!
3406 image saved to corresponding directory!
11552 DONE!
11552 image saved to corresponding directory!
16674 DONE!
16674 image saved to corresponding directory!
9937 DONE!
9937 image saved to corresponding directory!
12679 DONE!
12679 image saved to corresponding directory!
26965 DONE!
26965 image saved to corresponding directory!
10995 DONE!
10995 image saved to corresponding directory!
31659 DONE!
31659 image saved to corresponding directory!
8896 DONE!
8896 image saved to corresponding directory!
9961 DONE!
9961 image saved to corresponding directory!
29999 DONE!
29999 image 

/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/9937.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/12679.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/26965.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/10995.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats 

## Manipulations with features

In [20]:
@jit
def check_tumor(data, col): 
    indexes = []
    counter=0
    for i,y in enumerate(data.loc[:, col]): 
        if len(np.unique(y)) == 4:
            print(i)
            indexes.append(i)
            counter += 1
    print('All done!The number of images with tumors is {} and number of images without tumor is {}'.format(counter, len(data.index)-counter))
    return indexes

In [21]:
#Create folder with images on which tumor is presented 
@jit
def leave_only_tumors(data, col, ind, im_or_label = 'masks_train/'):
    
    
    for index, image in enumerate(data.loc[:, col]):
        if index in ind: 
            name=str(index)+'.png'
            io.imsave('/mnt/e/Image Processing/Brats Project/data/'+im_or_label+name, image)     
            print('{}.{} saved to corresponding directory!'.format(index, im_or_label))
            
            
            
    print('Finally, {} {} created'.format(index, im_or_label))

In [22]:
#creating train dataset
indexes = check_tumor(train, 'Y')

10
13
24
27
31
32
40
41
42
44
46
47
51
58
63
65
66
68
69
74
77
81
82
86
88
90
91
97
100
101
103
106
112
123
126
127
137
138
140
141
147
153
156
157
163
165
169
172
181
187
189
192
193
197
198
199
200
202
203
204
206
209
215
220
221
246
248
259
265
266
269
271
274
275
276
280
282
283
284
294
297
302
309
318
319
320
328
329
331
332
334
341
346
347
350
353
357
358
364
366
368
372
375
381
387
393
395
400
401
403
406
408
409
412
416
429
432
433
434
438
439
441
444
448
452
453
457
464
465
466
470
475
480
484
485
489
493
494
495
497
506
511
518
522
533
534
541
544
546
550
558
560
565
568
569
571
572
573
575
576
587
588
589
594
596
611
620
623
629
631
634
636
637
639
640
642
647
649
650
652
661
664
671
672
673
676
686
688
689
690
692
693
697
704
708
712
714
717
723
727
728
731
746
747
748
751
754
758
760
769
773
774
786
787
796
797
800
801
809
814
816
824
828
829
831
835
840
841
846
852
857
866
873
877
879
884
887
890
895
899
901
904
905
911
914
915
920
925
926
928
929
931
932
934
938
941
943


6505
6510
6519
6520
6527
6528
6529
6533
6539
6541
6555
6560
6563
6566
6571
6575
6578
6581
6582
6584
6585
6588
6590
6592
6595
6599
6601
6609
6613
6620
6626
6630
6631
6638
6644
6649
6650
6651
6652
6657
6659
6660
6661
6664
6669
6671
6673
6675
6678
6679
6681
6686
6692
6699
6702
6707
6709
6718
6723
6731
6736
6742
6743
6749
6754
6759
6760
6762
6766
6771
6772
6776
6778
6788
6794
6799
6802
6804
6806
6808
6810
6811
6812
6829
6835
6838
6855
6856
6860
6863
6865
6869
6871
6873
6875
6876
6877
6881
6884
6892
6894
6897
6902
6909
6910
6913
6916
6918
6922
6926
6930
6934
6935
6940
6951
6952
6957
6961
6962
6963
6974
6975
6977
6978
6979
6980
6983
6986
6991
7004
7006
7007
7017
7019
7028
7033
7041
7044
7047
7048
7049
7054
7056
7059
7065
7068
7070
7073
7074
7075
7081
7082
7084
7090
7092
7095
7099
7100
7106
7109
7114
7115
7116
7120
7121
7131
7135
7138
7141
7147
7151
7153
7154
7158
7159
7162
7166
7168
7169
7170
7171
7175
7177
7178
7181
7186
7188
7199
7201
7205
7207
7215
7217
7218
7222
7225
7226
7227
7230
7236


12663
12669
12671
12673
12674
12675
12677
12684
12695
12698
12700
12706
12714
12716
12719
12724
12726
12727
12729
12731
12750
12757
12763
12767
12773
12784
12791
12795
12800
12805
12806
12810
12815
12816
12817
12838
12844
12846
12847
12852
12853
12864
12866
12869
12874
12879
12882
12886
12893
12895
12902
12907
12908
12909
12914
12915
12919
12922
12923
12924
12933
12936
12940
12945
12946
12948
12956
12961
12974
12978
12980
12982
12983
12987
12988
12995
12998
12999
13001
13003
13005
13007
13008
13010
13011
13018
13030
13032
13045
13046
13047
13048
13050
13057
13059
13063
13064
13066
13067
13070
13073
13082
13093
13094
13095
13101
13107
13108
13109
13111
13116
13118
13121
13124
13127
13128
13141
13142
13144
13147
13158
13159
13160
13167
13168
13169
13176
13180
13187
13191
13193
13197
13199
13200
13203
13205
13206
13208
13210
13211
13222
13223
13228
13229
13235
13239
13242
13245
13246
13247
13255
13257
13258
13259
13266
13271
13278
13279
13282
13285
13287
13288
13293
13297
13298
13309
1331

17967
17969
17970
17971
17972
17983
17990
17991
18000
18001
18004
18009
18012
18014
18016
18019
18021
18022
18025
18026
18036
18040
18042
18043
18047
18048
18059
18060
18064
18067
18070
18073
18080
18082
18088
18091
18092
18093
18096
18098
18099
18106
18111
18116
18123
18125
18129
18130
18133
18139
18152
18154
18157
18162
18164
18166
18174
18176
18187
18188
18193
18195
18203
18206
18209
18212
18214
18219
18223
18237
18238
18240
18241
18246
18248
18250
18256
18257
18261
18262
18272
18273
18276
18278
18281
18287
18292
18296
18298
18299
18303
18325
18327
18331
18334
18344
18345
18349
18350
18353
18355
18361
18363
18366
18371
18378
18387
18391
18395
18397
18399
18401
18410
18414
18417
18422
18430
18441
18442
18450
18452
18453
18456
18457
18460
18470
18472
18473
18474
18481
18484
18489
18491
18492
18496
18497
18503
18510
18515
18530
18531
18536
18541
18551
18552
18557
18561
18562
18566
18567
18582
18585
18587
18588
18589
18590
18591
18594
18597
18599
18602
18606
18620
18626
18627
18631
1863

23263
23264
23267
23271
23277
23282
23287
23288
23289
23290
23294
23297
23301
23315
23317
23318
23323
23326
23328
23330
23331
23332
23334
23340
23342
23346
23350
23352
23356
23357
23360
23362
23367
23372
23373
23376
23379
23387
23393
23395
23398
23399
23400
23401
23407
23408
23410
23412
23416
23417
23419
23420
23430
23434
23438
23442
23447
23449
23451
23456
23462
23467
23468
23471
23476
23481
23482
23483
23487
23491
23493
23496
23502
23512
23518
23522
23527
23528
23529
23533
23541
23543
23545
23549
23552
23553
23558
23561
23566
23569
23572
23573
23580
23581
23588
23595
23596
23603
23605
23606
23608
23613
23619
23647
23649
23651
23654
23655
23656
23661
23663
23666
23668
23671
23674
23676
23677
23678
23688
23696
23704
23709
23714
23722
23724
23727
23728
23732
23746
23748
23750
23752
23753
23765
23767
23768
23769
23776
23777
23783
23785
23787
23788
23789
23792
23794
23795
23808
23810
23825
23826
23828
23829
23831
23833
23836
23842
23843
23849
23851
23852
23863
23868
23869
23879
23908
2390

In [23]:
#creating train dataset

leave_only_tumors(df, 'Y', ind=indexes)  #masks

leave_only_tumors(df, 'X',ind=indexes, im_or_label='images_train/') #images 

/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/10.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/13.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/24.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/27.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/dat

10.masks_train/ saved to corresponding directory!
13.masks_train/ saved to corresponding directory!
24.masks_train/ saved to corresponding directory!
27.masks_train/ saved to corresponding directory!
31.masks_train/ saved to corresponding directory!
32.masks_train/ saved to corresponding directory!
40.masks_train/ saved to corresponding directory!
41.masks_train/ saved to corresponding directory!
42.masks_train/ saved to corresponding directory!
44.masks_train/ saved to corresponding directory!
46.masks_train/ saved to corresponding directory!
47.masks_train/ saved to corresponding directory!
51.masks_train/ saved to corresponding directory!
58.masks_train/ saved to corresponding directory!
63.masks_train/ saved to corresponding directory!
65.masks_train/ saved to corresponding directory!
66.masks_train/ saved to corresponding directory!
68.masks_train/ saved to corresponding directory!
69.masks_train/ saved to corresponding directory!
74.masks_train/ saved to corresponding directory!


/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/358.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/364.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/366.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/368.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project

364.masks_train/ saved to corresponding directory!
366.masks_train/ saved to corresponding directory!
368.masks_train/ saved to corresponding directory!
372.masks_train/ saved to corresponding directory!
375.masks_train/ saved to corresponding directory!
381.masks_train/ saved to corresponding directory!
387.masks_train/ saved to corresponding directory!
393.masks_train/ saved to corresponding directory!
395.masks_train/ saved to corresponding directory!
400.masks_train/ saved to corresponding directory!
401.masks_train/ saved to corresponding directory!
403.masks_train/ saved to corresponding directory!
406.masks_train/ saved to corresponding directory!
408.masks_train/ saved to corresponding directory!
409.masks_train/ saved to corresponding directory!
412.masks_train/ saved to corresponding directory!
416.masks_train/ saved to corresponding directory!
429.masks_train/ saved to corresponding directory!
432.masks_train/ saved to corresponding directory!
433.masks_train/ saved to corre

/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/717.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/723.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/727.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_train/728.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project

...

27274.images_train/ saved to corresponding directory!
27275.images_train/ saved to corresponding directory!
27281.images_train/ saved to corresponding directory!
27284.images_train/ saved to corresponding directory!
27292.images_train/ saved to corresponding directory!
27294.images_train/ saved to corresponding directory!
27295.images_train/ saved to corresponding directory!
27296.images_train/ saved to corresponding directory!
27312.images_train/ saved to corresponding directory!
27315.images_train/ saved to corresponding directory!
27316.images_train/ saved to corresponding directory!
27320.images_train/ saved to corresponding directory!
27326.images_train/ saved to corresponding directory!
27327.images_train/ saved to corresponding directory!
27330.images_train/ saved to corresponding directory!
27334.images_train/ saved to corresponding directory!
27335.images_train/ saved to corresponding directory!
27338.images_train/ saved to corresponding directory!
27343.images_train/ saved to

/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/images_train/27430.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/images_train/27431.png is a low contrast image
  warn('%s is a low contrast image' % fname)


27522.images_train/ saved to corresponding directory!
27526.images_train/ saved to corresponding directory!
27530.images_train/ saved to corresponding directory!
27535.images_train/ saved to corresponding directory!
27536.images_train/ saved to corresponding directory!
27538.images_train/ saved to corresponding directory!
27539.images_train/ saved to corresponding directory!
27541.images_train/ saved to corresponding directory!
27544.images_train/ saved to corresponding directory!
27547.images_train/ saved to corresponding directory!
27548.images_train/ saved to corresponding directory!
27549.images_train/ saved to corresponding directory!
27550.images_train/ saved to corresponding directory!
27559.images_train/ saved to corresponding directory!
27560.images_train/ saved to corresponding directory!
27562.images_train/ saved to corresponding directory!
27564.images_train/ saved to corresponding directory!
27568.images_train/ saved to corresponding directory!
27574.images_train/ saved to

/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/images_train/27559.png is a low contrast image
  warn('%s is a low contrast image' % fname)


27661.images_train/ saved to corresponding directory!
27663.images_train/ saved to corresponding directory!
27669.images_train/ saved to corresponding directory!
27676.images_train/ saved to corresponding directory!
27681.images_train/ saved to corresponding directory!
27691.images_train/ saved to corresponding directory!
27694.images_train/ saved to corresponding directory!
27700.images_train/ saved to corresponding directory!
27702.images_train/ saved to corresponding directory!
27705.images_train/ saved to corresponding directory!
27706.images_train/ saved to corresponding directory!
27707.images_train/ saved to corresponding directory!
27710.images_train/ saved to corresponding directory!
27711.images_train/ saved to corresponding directory!
27717.images_train/ saved to corresponding directory!
27718.images_train/ saved to corresponding directory!
27728.images_train/ saved to corresponding directory!
27729.images_train/ saved to corresponding directory!
27730.images_train/ saved to

In [24]:
#test dataset 
for index, image in enumerate(test.loc[:, 'Y']):
    name=str(index)+'.png'
    io.imsave('/mnt/e/Image Processing/Brats Project/data/masks_test/'+name, image)     
    print('{}.{} saved to corresponding directory!'.format(index, '.png'))
    
for index, image in enumerate(test.loc[:, 'X']):
    name=str(index)+'.png'
    io.imsave('/mnt/e/Image Processing/Brats Project/data/images_test/'+name, image)     
    print('{}.{} saved to corresponding directory!'.format(index, '.png'))

0..png saved to corresponding directory!
1..png saved to corresponding directory!
2..png saved to corresponding directory!
3..png saved to corresponding directory!
4..png saved to corresponding directory!
5..png saved to corresponding directory!
6..png saved to corresponding directory!
7..png saved to corresponding directory!
8..png saved to corresponding directory!
9..png saved to corresponding directory!
10..png saved to corresponding directory!
11..png saved to corresponding directory!
12..png saved to corresponding directory!
13..png saved to corresponding directory!
14..png saved to corresponding directory!
15..png saved to corresponding directory!
16..png saved to corresponding directory!
17..png saved to corresponding directory!
18..png saved to corresponding directory!
19..png saved to corresponding directory!
20..png saved to corresponding directory!
21..png saved to corresponding directory!
22..png saved to corresponding directory!
23..png saved to corresponding directory!
24

/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_test/0.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_test/1.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_test/2.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_test/3.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_

100..png saved to corresponding directory!
101..png saved to corresponding directory!
102..png saved to corresponding directory!
103..png saved to corresponding directory!
104..png saved to corresponding directory!
105..png saved to corresponding directory!
106..png saved to corresponding directory!
107..png saved to corresponding directory!
108..png saved to corresponding directory!
109..png saved to corresponding directory!
110..png saved to corresponding directory!
111..png saved to corresponding directory!
112..png saved to corresponding directory!
113..png saved to corresponding directory!
114..png saved to corresponding directory!
115..png saved to corresponding directory!
116..png saved to corresponding directory!
117..png saved to corresponding directory!
118..png saved to corresponding directory!
119..png saved to corresponding directory!
120..png saved to corresponding directory!
121..png saved to corresponding directory!
122..png saved to corresponding directory!
123..png sa

/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_test/107.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_test/108.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_test/109.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/masks_test/110.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/dat

219..png saved to corresponding directory!
220..png saved to corresponding directory!
221..png saved to corresponding directory!
222..png saved to corresponding directory!
223..png saved to corresponding directory!
224..png saved to corresponding directory!
225..png saved to corresponding directory!
226..png saved to corresponding directory!
227..png saved to corresponding directory!
228..png saved to corresponding directory!
229..png saved to corresponding directory!
230..png saved to corresponding directory!
231..png saved to corresponding directory!
232..png saved to corresponding directory!
233..png saved to corresponding directory!
234..png saved to corresponding directory!
235..png saved to corresponding directory!
236..png saved to corresponding directory!
237..png saved to corresponding directory!
238..png saved to corresponding directory!
239..png saved to corresponding directory!
240..png saved to corresponding directory!
241..png saved to corresponding directory!
242..png sa

...

/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/images_test/9117.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/images_test/9122.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/images_test/9128.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/images_test/9143.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Pro

9131..png saved to corresponding directory!
9132..png saved to corresponding directory!
9133..png saved to corresponding directory!
9134..png saved to corresponding directory!
9135..png saved to corresponding directory!
9136..png saved to corresponding directory!
9137..png saved to corresponding directory!
9138..png saved to corresponding directory!
9139..png saved to corresponding directory!
9140..png saved to corresponding directory!
9141..png saved to corresponding directory!
9142..png saved to corresponding directory!
9143..png saved to corresponding directory!
9144..png saved to corresponding directory!
9145..png saved to corresponding directory!
9146..png saved to corresponding directory!
9147..png saved to corresponding directory!
9148..png saved to corresponding directory!
9149..png saved to corresponding directory!
9150..png saved to corresponding directory!
9151..png saved to corresponding directory!
9152..png saved to corresponding directory!
9153..png saved to corresponding

/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/images_test/9190.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/images_test/9200.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/images_test/9208.png is a low contrast image
  warn('%s is a low contrast image' % fname)
/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/images_test/9226.png is a low contrast image
  warn('%s is a low contrast image' % fname)


9214..png saved to corresponding directory!
9215..png saved to corresponding directory!
9216..png saved to corresponding directory!
9217..png saved to corresponding directory!
9218..png saved to corresponding directory!
9219..png saved to corresponding directory!
9220..png saved to corresponding directory!
9221..png saved to corresponding directory!
9222..png saved to corresponding directory!
9223..png saved to corresponding directory!
9224..png saved to corresponding directory!
9225..png saved to corresponding directory!
9226..png saved to corresponding directory!
9227..png saved to corresponding directory!
9228..png saved to corresponding directory!
9229..png saved to corresponding directory!
9230..png saved to corresponding directory!
9231..png saved to corresponding directory!
9232..png saved to corresponding directory!
9233..png saved to corresponding directory!
9234..png saved to corresponding directory!
9235..png saved to corresponding directory!
9236..png saved to corresponding

/home/andrii/anaconda3/lib/python3.7/site-packages/skimage/io/_io.py:140: UserWarning: /mnt/e/Image Processing/Brats Project/data/images_test/9247.png is a low contrast image
  warn('%s is a low contrast image' % fname)


## Making different classes of images 

In [ ]:
for i,y in enumerate(df.loc[:, 'X']): 
    
    name=str(i)+'.png'
    io.imsave('/mnt/e/Image Processing/Brats Project/data/images_full/'+name, y)
    print("{} saved to PATH as {}".format(i, name))

In [ ]:
def make_class(data, cl,PATH, col='Y'):
    for i,y in enumerate(data.loc[:, col]):
            a=np.copy(y)
            a[a != cl] = 0
                        
            name=str(cl)+'_'+str(i)+'.png'
            io.imsave(PATH+name, a)
            print("{} saved to PATH as {}".format(i, name))

In [ ]:
make_class(df, cl=1, PATH='e://Image Processing/Brats Project/data/masks/1/')
make_class(df, cl=2, PATH='e://Image Processing/Brats Project/data/masks/2/')
make_class(df, cl=4, PATH='e://Image Processing/Brats Project/data/masks/4/')

In [ ]:
#separate arrays for each masks

def make_mask(data, col, clas):
    data[str(clas)]=0
    data[str(clas)]=data[str(clas)].apply(lambda x: np.empty((data.loc[0, col].shape), dtype='uint8'))
    
    for i,y in enumerate(data.loc[:, col]):
        
        a=np.copy(y)
        a[a != clas] = 0
        a[a == clas] = 1
        data.at[i, str(clas)] = a

In [ ]:
make_mask(df, 'Y', 1)
make_mask(df, 'Y', 2)
make_mask(df, 'Y', 4)

In [ ]:
final_df=df.loc[:, ['X', '1', '2', '4']]

In [ ]:
final_df.columns

In [ ]:
final_df.to_pickle('./im+masks.pkl')